Convert AmyStyle training data to a simple JSONL format

In [53]:
import xml.etree.ElementTree as ET
import json
import regex as re
import glob
import os

def xml_to_jsonl(input_xml_path, output_jsonl_path, tags):
    tree = ET.parse(input_xml_path)
    root = tree.getroot()

    with (open(output_jsonl_path, 'w', encoding='utf-8') as f):
        for sequence in root.findall('sequence'):
            output = []
            for element in sequence:
                for tag in tags:
                    fn = None
                    if type(tag) is tuple:
                        tag, fn = tag
                    if element.tag == tag:
                        value = fn(element.text) if callable(fn) else element.text
                        is_new_ref = (len(output) == 0 #  if no refs yet
                                     or tag == "citation-number" 
                                     or tag in output[-1] # or tag already exists
                                     or (tag in ["author", "editor", "authority", "legal-ref"] and 'date' in output[-1])) # or a creator field follows a date field 
                        if is_new_ref:
                            output.append({})
                            # add citation number from previous citation 
                            if len(output) > 1 and 'citation-number' in tags and tag != "citation-number" and 'citation-number' in output[-2]:
                                output[-1]['citation-number'] = output[-2]['citation-number']
                        # merge tags
                        if tag == "authority":
                            tag = "author"                       
                        output[-1][tag] = value
            if len(output) > 0:
                instance = {
                    "in" : " ".join(element.text.strip() if element.text else '' for element in sequence),
                    "out" : output
                }
                f.write(json.dumps(instance) + '\n')

def remove_punctuation(text):
    start, end = 0, len(text)
    while start < len(text) and re.match("\p{P}", text[start]) and text[start] not in ")]":
        start += 1
    while end > start and re.match("\p{P}", text[end - 1]) and text[end - 1] not in ")]":
        end -= 1
    return text[start:end].strip()

def clean_editor(text):
    text = re.sub(r'în:? ?', '', text.strip(), flags=re.IGNORECASE)
    text = re.sub(r'hrsg\. v\.|hg\. v|hrsg|ed\.|eds\.', '', text, flags=re.IGNORECASE)
    return remove_punctuation(text)

def clean_container(text):
    return remove_punctuation(re.sub(r'^(in|aus|from)(:| )', '', text.strip(), flags=re.IGNORECASE))
    
def extract_year(text): 
    m = re.search( r'[12][0-9]{3}', text)
    return m.group(0) if m else None

for input_file in glob.glob('in/*.xml'):
    base_name = os.path.basename(input_file)
    output_file = f'out/{os.path.splitext(base_name)[0]}.jsonl'
    print(f'Processing {input_file}')
    xml_to_jsonl(input_file, output_file, [
        'citation-number',
        ("author", remove_punctuation),
        ("editor", clean_editor),
        ("authority", remove_punctuation),
        ("title", remove_punctuation),
        ("legal-ref", remove_punctuation),
        ("container-title", clean_container),
        ("journal", clean_container),
        ("date", extract_year),
        ("backref", remove_punctuation)
    ])



Processing in\10.1111_1467-6478.00057.xml
Processing in\10.1111_1467-6478.00080.xml
Processing in\10.1515_zfrs-1980-0103.xml
Processing in\10.1515_zfrs-1980-0104.xml
